In [2]:
import numpy as np
import pandas as pd
import pickle

import plotly.graph_objects as go

In [3]:
with open("../pipeline/data/ret1_data.pkl", "rb") as file:
    ret_data = pickle.load(file)
len(ret_data)

16

In [5]:
num_spike_group = 0
for session in ret_data:
    print('---------------------------------------')
    print('Subject Name:', session['subject_name'])
    print('Sample Number:', session['sample_number'])
    print('Session Date:', session['session_date'])
    print('-------------------')
    for stimulation_example in session['stimulations']:
        print("Stimulation screen size/px: {}*{}".format(stimulation_example['stim_width'], stimulation_example['stim_height']))
        print("Block size/px: {}*{}".format(stimulation_example['x_block_size'], stimulation_example['y_block_size']))
        print("Pixel size on retina: {}".format(stimulation_example['pixel_size']))
        print("Movie shape/blocks: {}, n_frames: {}, FPS: {}, so movie time is {}".format(stimulation_example['movie'].shape, stimulation_example['n_frames'], stimulation_example['fps'], round(stimulation_example['n_frames']/stimulation_example['fps'], 4)))
        print("Onset of the stimulus from the beginning of the recording session in seconds: {}".format(stimulation_example['stimulus_onset']))
        print("Total session time should be stimulus onset + movie time: {} ?".format(round(stimulation_example['n_frames']/stimulation_example['fps']+stimulation_example['stimulus_onset'], 4)))
        print("Spikes detected at how many seconds from the beginning of the recording: ")
        for spike in stimulation_example['spikes']:
            print(spike.shape, max(spike.flatten()))
            num_spike_group += 1
        print('-------------------')
print(num_spike_group)

---------------------------------------
Subject Name: KO (chx10)
Sample Number: 1
Session Date: 2008-06-06
-------------------
Stimulation screen size/px: 640*480
Block size/px: 1*480
Pixel size on retina: 8.3
Movie shape/blocks: (640, 1, 3823), n_frames: 3823, FPS: 59.9815, so movie time is 63.7363
Onset of the stimulus from the beginning of the recording session in seconds: 1.65657
Total session time should be stimulus onset + movie time: 65.3929 ?
Spikes detected at how many seconds from the beginning of the recording: 
(32, 1) 64.9341
(109, 1) 65.9543
(168, 1) 65.5169
(245, 1) 66.3438
-------------------
---------------------------------------
Subject Name: KO (chx10)
Sample Number: 2
Session Date: 2008-06-06
-------------------
Stimulation screen size/px: 640*480
Block size/px: 640*1
Pixel size on retina: 8.3
Movie shape/blocks: (1, 480, 4377), n_frames: 4377, FPS: 59.9815, so movie time is 72.9725
Onset of the stimulus from the beginning of the recording session in seconds: 1.772

---

#### Set Session Index, Stimulation Index, Spike Index

In [176]:
example_session_idx = 0
example_stimulation_idx = 0
example_spike_idx = 0
example_stimulation = ret_data[example_session_idx]['stimulations'][example_stimulation_idx]
example_movie = ret_data[example_session_idx]['stimulations'][example_stimulation_idx]['movie']
example_one_spike = ret_data[example_session_idx]['stimulations'][example_stimulation_idx]['spikes'][example_spike_idx]

In [177]:
# Get spike detected time vs movie playing time = each spike detected time - stimulus onset
spike_time_movie_time = example_one_spike-example_stimulation['stimulus_onset']
print(spike_time_movie_time)

[[ 0.81173]
 [ 0.91613]
 [ 0.95223]
 [ 8.39093]
 [15.82923]
 [15.94713]
 [15.96413]
 [17.44103]
 [17.54333]
 [22.63513]
 [27.89813]
 [27.91583]
 [27.94113]
 [32.10933]
 [35.38433]
 [36.11703]
 [38.31923]
 [38.45053]
 [40.29323]
 [41.40563]
 [43.36593]
 [45.45663]
 [46.94743]
 [48.68003]
 [48.79613]
 [50.07353]
 [57.20043]
 [59.90423]
 [62.05353]
 [62.11023]
 [62.19103]
 [63.27753]]


In [178]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=list(spike_time_movie_time.flatten()), y=[1]*len(spike_time_movie_time), 
                mode='markers', marker=dict(size=3), name='Spike Detection',
                hovertemplate = 'Spike is detected at %{x:.4f} seconds <br>when movie starts to play',)
)
fig.update_layout(title='Spike Detection vs Movie Time (exclude stimulus_onset)', xaxis_title='Time/s', yaxis_title='Spike Detected Indicator', showlegend=True)
fig.show()

In [179]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(x=list(spike_time_movie_time.flatten()*example_stimulation['fps']), y=[1]*len(spike_time_movie_time), 
                mode='markers', marker=dict(size=3), name='Spike Detection',
                hovertemplate = 'Spike is detected at %{x:.0f} movie frame',)
)
fig.update_layout(title='Spike Detection vs Movie Frame (exclude stimulus_onset)', xaxis_title='Number of frames', yaxis_title='Spike Detected Indicator', showlegend=True)
fig.show()

In [180]:
print("Stimulation screen size/px: {}*{}".format(example_stimulation['stim_width'], example_stimulation['stim_height']))
print("Block size/px: {}*{}".format(example_stimulation['x_block_size'], example_stimulation['y_block_size']))
print("Movie shape/blocks: {}, n_frames: {}, FPS: {}, so movie time is {}".format(example_stimulation['movie'].shape, example_stimulation['n_frames'], example_stimulation['fps'], round(example_stimulation['n_frames']/example_stimulation['fps'], 4)))

Stimulation screen size/px: 640*480
Block size/px: 1*480
Movie shape/blocks: (640, 1, 3823), n_frames: 3823, FPS: 59.9815, so movie time is 63.7363


#### Set Frame Index

In [197]:
# from a number of frame to get how does the stimulation screen looks like at that frame
# make a 2d array as a screen -> using heatmap to visualize
n_frames = 49
screen_at_this_frame = np.zeros((example_stimulation['stim_width'], example_stimulation['stim_height']))
for block_x in range(int(example_stimulation['stim_width']/example_stimulation['x_block_size'])):
    for block_y in range(int(example_stimulation['stim_height']/example_stimulation['y_block_size'])):
        is_block_active = True if example_movie[block_x][block_y][n_frames] > 0 else False
        # print(block_x, block_y, n_frames, is_block_active)
        screen_x_from = block_x*example_stimulation['x_block_size']
        screen_x_to = (block_x+1)*example_stimulation['x_block_size']
        screen_y_from = block_y*example_stimulation['y_block_size']
        screen_y_to = (block_y+1)*example_stimulation['y_block_size']
        # print("x {}~{} y {}~{}".format(screen_x_from, screen_x_to, screen_y_from, screen_y_to))
        if is_block_active:
            screen_at_this_frame[screen_x_from:screen_x_to, screen_y_from:screen_y_to] = 100
screen_at_this_frame = screen_at_this_frame.T
screen_at_this_frame

array([[  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.],
       ...,
       [  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.]])

In [208]:
fig = go.Figure(data=go.Heatmap(
                    z=screen_at_this_frame,
                    colorscale='greys'))
fig.update_layout(title='How the movie looks like at {} frame'.format(n_frames),
                    xaxis_title='stimulus_width {}'.format(example_stimulation['stim_width']),
                    yaxis_title='stimulus_height {}'.format(example_stimulation['stim_height']),
                    hovermode=False)
fig.update_traces(showscale=False)
fig.show()

In [211]:
def get_frame(stimulation:dict, movie:np.ndarray, n_frames:int)->np.ndarray:
    """
    Get a 2d array of a movie frame

    :param stimulation: stimulation dictionary
    :param movie: stimulation movie 3d array (horizontal_blocks, vertical_blocks, frames)
    :param n_frames: the number of a frame in the movie
    """
    screen_at_this_frame = np.zeros((example_stimulation['stim_width'], example_stimulation['stim_height']))
    for block_x in range(int(example_stimulation['stim_width']/example_stimulation['x_block_size'])):
        for block_y in range(int(example_stimulation['stim_height']/example_stimulation['y_block_size'])):
            is_block_active = True if example_movie[block_x][block_y][n_frames] > 0 else False
            # print(block_x, block_y, n_frames, is_block_active)
            screen_x_from = block_x*example_stimulation['x_block_size']
            screen_x_to = (block_x+1)*example_stimulation['x_block_size']
            screen_y_from = block_y*example_stimulation['y_block_size']
            screen_y_to = (block_y+1)*example_stimulation['y_block_size']
            # print("x {}~{} y {}~{}".format(screen_x_from, screen_x_to, screen_y_from, screen_y_to))
            if is_block_active:
                screen_at_this_frame[screen_x_from:screen_x_to, screen_y_from:screen_y_to] = 100
    return screen_at_this_frame.T

example_frame = get_frame(example_stimulation, example_movie, n_frames)
example_frame

array([[  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.],
       ...,
       [  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.],
       [  0.,   0., 100., ...,   0., 100., 100.]])

In [229]:
def plot_frame(n_frames:int, frame:np.ndarray):
    """
    Plot a frame

    :param n_frames: the number of a frame
    :param frame: a 2d array of a frame
    """
    height, width = frame.shape
    fig = go.Figure(data=go.Heatmap(
                    z=frame,
                    colorscale='greys'))
    fig.update_layout(title='How the movie looks like at {} frame'.format(n_frames),
                        xaxis_title='stimulus_width {}'.format(width),
                        yaxis_title='stimulus_height {}'.format(height),
                        hovermode=False)
    fig.update_traces(showscale=False)
    fig.show()

# plot_frame(n_frames, example_frame)

#### Set the Numbers of Delay Frames

In [218]:
n_frames_of_delay = 5
delay_of_frames = []
for n in range(n_frames_of_delay):
    delay_of_frames.append(get_frame(example_stimulation, example_movie, n_frames-n))
delay_of_frames = np.array(delay_of_frames)
delay_of_frames

array([[[  0.,   0., 100., ...,   0., 100., 100.],
        [  0.,   0., 100., ...,   0., 100., 100.],
        [  0.,   0., 100., ...,   0., 100., 100.],
        ...,
        [  0.,   0., 100., ...,   0., 100., 100.],
        [  0.,   0., 100., ...,   0., 100., 100.],
        [  0.,   0., 100., ...,   0., 100., 100.]],

       [[  0.,   0.,   0., ..., 100.,   0., 100.],
        [  0.,   0.,   0., ..., 100.,   0., 100.],
        [  0.,   0.,   0., ..., 100.,   0., 100.],
        ...,
        [  0.,   0.,   0., ..., 100.,   0., 100.],
        [  0.,   0.,   0., ..., 100.,   0., 100.],
        [  0.,   0.,   0., ..., 100.,   0., 100.]],

       [[  0.,   0.,   0., ...,   0.,   0., 100.],
        [  0.,   0.,   0., ...,   0.,   0., 100.],
        [  0.,   0.,   0., ...,   0.,   0., 100.],
        ...,
        [  0.,   0.,   0., ...,   0.,   0., 100.],
        [  0.,   0.,   0., ...,   0.,   0., 100.],
        [  0.,   0.,   0., ...,   0.,   0., 100.]],

       [[100.,   0., 100., ...,   0.,

In [221]:
sta = np.average(delay_of_frames, axis=0)
sta

array([[40.,  0., 40., ..., 40., 60., 80.],
       [40.,  0., 40., ..., 40., 60., 80.],
       [40.,  0., 40., ..., 40., 60., 80.],
       ...,
       [40.,  0., 40., ..., 40., 60., 80.],
       [40.,  0., 40., ..., 40., 60., 80.],
       [40.,  0., 40., ..., 40., 60., 80.]])

In [228]:
def plot_sta(n_frames:int, n_frames_of_delay:int, sta:np.ndarray):
    """
    Plot a STA of several delays of a frame

    :param n_frames: the number of a frame
    :param n_delays: how many delays of a frame i.e. n_delays=5 from frame 49 -> 49, 48, 47, 46, 45 
    :param frame: a 2d array of a frame
    """
    height, width = sta.shape
    fig = go.Figure(data=go.Heatmap(
                    z=sta,
                    colorscale='greys'))
    fig.update_layout(title='How the STA looks like of the {} frame with {} numbers of delay frames'.format(n_frames, n_frames_of_delay),
                        xaxis_title='stimulus_width {}'.format(width),
                        yaxis_title='stimulus_height {}'.format(height),
                        hovermode=False)
    fig.update_traces(showscale=False)
    fig.show()
    
plot_sta(n_frames, n_frames_of_delay, sta)